In [ ]:
!git clone https://github.com/nateraw/huggingface-vit-finetune.git
!pip install adversarial-robustness-toolbox
!pip install timm
%cd huggingface-vit-finetune/
!pip install -r requirements.txt
!pip install git+https://github.com/huggingface/transformers.git@master --upgrade

Cloning into 'huggingface-vit-finetune'...
remote: Enumerating objects: 24, done.
remote: Counting objects: 100% (24/24), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 24 (delta 10), reused 19 (delta 6), pack-reused 0
Unpacking objects: 100% (24/24), done.
/content/huggingface-vit-finetune/huggingface-vit-finetune
  Cloning https://github.com/huggingface/transformers.git (to revision master) to /tmp/pip-req-build-fimawm8f
  Running command git clone -q https://github.com/huggingface/transformers.git /tmp/pip-req-build-fimawm8f
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for transformers: filename=transformers-4.6.0.dev0-cp37-none-any.whl size=2107872 sha256=a65012f23ba955a84c6e6378f63f0e29332d89954c25f9c8acf485f9845d074f
  Stored in directory: /tmp/pip-ephem-wheel-cache-xnov65ig/wheels/03/01/00/f2c9020459e177a2729b25f0b9628d95bb967727d71a118170
Successfully built tra

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader

import torchvision
import torchvision.transforms as transforms
import torchvision.datasets as datasets

import matplotlib
import matplotlib.pyplot as plt
import numpy as np

import art
from art.attacks.evasion import FastGradientMethod, ProjectedGradientDescentPyTorch
from art.estimators.classification import PyTorchClassifier

from transformers import ViTFeatureExtractor, ViTForImageClassification
import requests

import timm
from timm.data import resolve_data_config
from timm.data.transforms_factory import create_transform

In [ ]:
result_dict = {}
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

In [ ]:
transform = transforms.Compose(
    [
      # transforms.Resize((224, 224)),
      transforms.ToTensor(),
      # transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
    ])
cifar_trainset = datasets.CIFAR10(root='./data', train=True, download=True, transform=transform)
cifar_testset = datasets.CIFAR10(root='./data', train=False, download=True, transform=transform)
cifar_trainloader = torch.utils.data.DataLoader(cifar_trainset, batch_size=64, shuffle=True, num_workers=2)
cifar_testloader = torch.utils.data.DataLoader(cifar_testset, batch_size=64, shuffle=False, num_workers=2)
cifar_classes = [
    'airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck'
]


Extracting ./data/cifar-10-python.tar.gz to ./data
Files already downloaded and verified


In [ ]:
model = ViTForImageClassification.from_pretrained('nateraw/vit-base-patch16-224-cifar10', return_dict=False)
model.to(device)
model = nn.Sequential(
    nn.Upsample(scale_factor=7, mode='bilinear'),
    model
)
model

Sequential(
  (0): Upsample(scale_factor=7.0, mode=bilinear)
  (1): ViTForImageClassification(
    (vit): ViTModel(
      (embeddings): ViTEmbeddings(
        (patch_embeddings): PatchEmbeddings(
          (projection): Conv2d(3, 768, kernel_size=(16, 16), stride=(16, 16))
        )
        (dropout): Dropout(p=0.0, inplace=False)
      )
      (encoder): ViTEncoder(
        (layer): ModuleList(
          (0): ViTLayer(
            (attention): ViTAttention(
              (attention): ViTSelfAttention(
                (query): Linear(in_features=768, out_features=768, bias=True)
                (key): Linear(in_features=768, out_features=768, bias=True)
                (value): Linear(in_features=768, out_features=768, bias=True)
                (dropout): Dropout(p=0.0, inplace=False)
              )
              (output): ViTSelfOutput(
                (dense): Linear(in_features=768, out_features=768, bias=True)
                (dropout): Dropout(p=0.0, inplace=False)
             

In [ ]:
# cifar-10 DATASET consists of 60000 images
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = model(inputs)
    _, predicted = torch.max(outputs[0], 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


Accuracy of the network on 64 cifar-10 test images: 100.000000 %
Accuracy of the network on 704 cifar-10 test images: 99.573864 %
Accuracy of the network on 1344 cifar-10 test images: 99.330357 %
Accuracy of the network on 1984 cifar-10 test images: 99.243952 %
Accuracy of the network on 2624 cifar-10 test images: 99.161585 %
Accuracy of the network on 3264 cifar-10 test images: 99.172794 %
Accuracy of the network on 3904 cifar-10 test images: 99.103484 %
Accuracy of the network on 4544 cifar-10 test images: 99.031690 %
Accuracy of the network on 5184 cifar-10 test images: 98.900463 %
Accuracy of the network on 5824 cifar-10 test images: 98.849588 %
Accuracy of the network on 6464 cifar-10 test images: 98.855198 %
Accuracy of the network on 7104 cifar-10 test images: 98.789414 %
Accuracy of the network on 7744 cifar-10 test images: 98.747417 %
Accuracy of the network on 8384 cifar-10 test images: 98.687977 %
Accuracy of the network on 9024 cifar-10 test images: 98.736702 %
Accuracy of 

In [ ]:
class Transformer(nn.Module):
  def __init__(self, model):
    super(Transformer, self).__init__()
    self.model = model
  def forward(self, x):
    return model(x)[0]

Transformer_Model = Transformer(model).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
transformer_classifier = PyTorchClassifier(
    model=Transformer_Model.cpu(),
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 32, 32),
    nb_classes=10,
)

In [ ]:
CNN_Model = torch.hub.load("chenyaofo/pytorch-cifar-models", "cifar10_vgg16_bn", pretrained=True)
CNN_Model = CNN_Model.to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
cnn_classifier = PyTorchClassifier(
    model=CNN_Model,
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 32, 32),
    nb_classes=10,
)

Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/archive/master.zip" to /root/.cache/torch/hub/master.zip
Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/releases/download/vgg/cifar10_vgg16_bn-6ee7ea24.pt" to /root/.cache/torch/hub/checkpoints/cifar10_vgg16_bn-6ee7ea24.pt


In [ ]:
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = CNN_Model(inputs)
    _, predicted = torch.max(outputs, 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 90.625000 %
Accuracy of the network on 704 cifar-10 test images: 94.602273 %
Accuracy of the network on 1344 cifar-10 test images: 93.750000 %
Accuracy of the network on 1984 cifar-10 test images: 92.993952 %
Accuracy of the network on 2624 cifar-10 test images: 92.568598 %
Accuracy of the network on 3264 cifar-10 test images: 92.892157 %
Accuracy of the network on 3904 cifar-10 test images: 92.674180 %
Accuracy of the network on 4544 cifar-10 test images: 92.825704 %
Accuracy of the network on 5184 cifar-10 test images: 92.785494 %
Accuracy of the network on 5824 cifar-10 test images: 92.788462 %
Accuracy of the network on 6464 cifar-10 test images: 92.806312 %
Accuracy of the network on 7104 cifar-10 test images: 92.849099 %
Accuracy of the network on 7744 cifar-10 test images: 92.858988 %
Accuracy of the network on 8384 cifar-10 test images: 92.891221 %
Accuracy of the network on 9024 cifar-10 test images: 92.796986 %
Accuracy of t

# Attack CNN model

In [ ]:
eps = 0.05
attack_PGD_1 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-1 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_1"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 39.062500 %


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 704 cifar-10 test images: 32.812500 %


Accuracy of the network on 1344 cifar-10 test images: 33.779762 %


Accuracy of the network on 1984 cifar-10 test images: 34.072581 %


...

Accuracy of the network on 7744 cifar-10 test images: 33.070764 %


Accuracy of the network on 8384 cifar-10 test images: 32.848282 %


Accuracy of the network on 9024 cifar-10 test images: 32.734929 %


Accuracy of the network on 9664 cifar-10 test images: 32.760762 %


Accuracy of the network on 10000 cifar-10 test images: 32.710000 %


In [ ]:
attack_PGD_5 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-5 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_5"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 4.687500 %


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 704 cifar-10 test images: 3.551136 %


Accuracy of the network on 1344 cifar-10 test images: 4.464286 %


Accuracy of the network on 1984 cifar-10 test images: 4.586694 %


...

Accuracy of the network on 7744 cifar-10 test images: 4.235537 %


Accuracy of the network on 8384 cifar-10 test images: 4.210401 %


Accuracy of the network on 9024 cifar-10 test images: 4.255319 %


Accuracy of the network on 9664 cifar-10 test images: 4.201159 %


Accuracy of the network on 10000 pgd-5 cifar-10 test images: 4.170000 %


In [ ]:
attack_PGD_10 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-10 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_10"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 4.687500 %


Accuracy of the network on 704 cifar-10 test images: 3.125000 %


Accuracy of the network on 1344 cifar-10 test images: 4.092262 %


Accuracy of the network on 1984 cifar-10 test images: 4.183468 %


...

Accuracy of the network on 7744 cifar-10 test images: 3.925620 %


Accuracy of the network on 8384 cifar-10 test images: 3.900286 %


Accuracy of the network on 9024 cifar-10 test images: 3.945035 %


Accuracy of the network on 9664 cifar-10 test images: 3.911424 %


Accuracy of the network on 10000 pgd-10 cifar-10 test images: 3.890000 %


In [ ]:
attack_PGD_20 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20.generate(x=inputs)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-20 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 4.687500 %


Accuracy of the network on 704 cifar-10 test images: 3.551136 %


Accuracy of the network on 1344 cifar-10 test images: 4.166667 %


Accuracy of the network on 1984 cifar-10 test images: 4.385081 %


...

Accuracy of the network on 7744 cifar-10 test images: 4.196798 %


Accuracy of the network on 8384 cifar-10 test images: 4.150763 %


Accuracy of the network on 9024 cifar-10 test images: 4.177748 %


Accuracy of the network on 9664 cifar-10 test images: 4.149421 %


Accuracy of the network on 10000 pgd-20 cifar-10 test images: 4.130000 %


# Attack Transformer

In [ ]:
attack_PGD_1 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-1 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_1"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 53.125000 %


Accuracy of the network on 704 cifar-10 test images: 48.295455 %


Accuracy of the network on 1344 cifar-10 test images: 49.404762 %


...

Accuracy of the network on 7744 cifar-10 test images: 48.476240 %


Accuracy of the network on 8384 cifar-10 test images: 48.544847 %


Accuracy of the network on 9024 cifar-10 test images: 48.238032 %


Accuracy of the network on 9664 cifar-10 test images: 48.365066 %


Accuracy of the network on 10000 pgd-1 cifar-10 test images: 48.260000 %


In [ ]:
attack_PGD_5 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-5 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_5"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 3.125000 %


Accuracy of the network on 704 cifar-10 test images: 1.988636 %


Accuracy of the network on 1344 cifar-10 test images: 1.562500 %


...

Accuracy of the network on 7744 cifar-10 test images: 2.091942 %


Accuracy of the network on 8384 cifar-10 test images: 2.039599 %


Accuracy of the network on 9024 cifar-10 test images: 2.016844 %


Accuracy of the network on 9664 cifar-10 test images: 2.069536 %


Accuracy of the network on 10000 cifar-10 test images: 2.070000 %


In [ ]:
attack_PGD_10 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-10 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_10"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 0.000000 %


Accuracy of the network on 704 cifar-10 test images: 0.426136 %


Accuracy of the network on 1344 cifar-10 test images: 0.372024 %


...

Accuracy of the network on 7744 cifar-10 test images: 0.839360 %


Accuracy of the network on 8384 cifar-10 test images: 0.858779 %


Accuracy of the network on 9024 cifar-10 test images: 0.853280 %


Accuracy of the network on 9664 cifar-10 test images: 0.869205 %


Accuracy of the network on 10000 pgd-10 cifar-10 test images: 0.860000 %


In [ ]:
attack_PGD_20 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20.generate(x=inputs)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d pgd-20 cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:3458: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode)


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 0.000000 %


Accuracy of the network on 704 cifar-10 test images: 0.426136 %


Accuracy of the network on 1344 cifar-10 test images: 0.520833 %


...

Accuracy of the network on 7744 cifar-10 test images: 0.736054 %


Accuracy of the network on 8384 cifar-10 test images: 0.775286 %


Accuracy of the network on 9024 cifar-10 test images: 0.753546 %


Accuracy of the network on 9664 cifar-10 test images: 0.765728 %


Accuracy of the network on 10000 pgd-20 cifar-10 test images: 0.770000 %


In [ ]:
result_dict

{'CNN': 92.86,
 'CNN_PGD_1': 32.71,
 'CNN_PGD_10': 3.89,
 'CNN_PGD_20': 4.13,
 'CNN_PGD_5': 4.17,
 'Transformer': 98.74,
 'Transformer_PGD_1': 48.26,
 'Transformer_PGD_10': 0.86,
 'Transformer_PGD_20': 0.77,
 'Transformer_PGD_5': 2.07}

FGSMAttack

In [ ]:
attack_FGM = FastGradientMethod(estimator=transformer_classifier, eps=eps)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_FGM.generate(x=inputs)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))

In [ ]:
attack_FGM = FastGradientMethod(estimator=cnn_classifier, eps=eps)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_FGM.generate(x=inputs)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))